# Search and Filter DataFrames in PySpark HW

Now it's time to put what you've learn into action with a homework assignment!

In case you need it again, here is the link to the documentation for the full list available function in pyspark.sql.functions library:
http://spark.apache.org/docs/latest/api/python/pyspark.sql.html#module-pyspark.sql.functions


### First set up your Spark Session!
Alright so first things first, let's start up our pyspark instance.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
path = "drive/MyDrive/5. Spark/spark-scripts/section2/Datasets/"

In [ ]:
!pip install pyspark
import pyspark

from pyspark.sql import SparkSession
spark = SparkSession.builder.appName('select&filter').getOrCreate()
spark

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 281.4/281.4 MB 4.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.7/199.7 KB 14.5 MB/s eta 0:00:00
  Created wheel for pyspark: filename=pyspark-3.3.1-py2.py3-none-any.whl size=281845512 sha256=c17c603d7de44bf2d1b547ccb800d2143ec01ee98eb9a66a94e9dddfb5dad33d
  Stored in directory: /root/.cache/pip/wheels/43/dc/11/ec201cd671da62fa9c5cc77078235e40722170ceba231d7598
Successfully built pyspark


## Read in the DataFrame for this Notebook

We will be continuing to use the fifa19.csv file for this notebook. Make sure that you are writting the correct path to the file. 

In [ ]:
df = spark.read.csv(path+'fifa19.csv',inferSchema=True,header=True)

## About this dataframe

The **fifa19.csv** dataset includes a list of all the FIFA 2019 players and their attributes listed below: 

 - **General**: Age, Nationality, Overall, Potential, Club
 - **Metrics:** Value, Wage
 - **Player Descriptive:** Preferred Foot, International Reputation, Weak Foot, Skill Moves, Work Rate, Position, Jersey Number, Joined, Loaned From, Contract Valid Until, Height, Weight
 - **Possition:** LS, ST, RS, LW, LF, CF, RF, RW, LAM, CAM, RAM, LM, LCM, CM, RCM, RM, LWB, LDM, CDM, RDM, RWB, LB, LCB, CB, RCB, RB, 
 - **Other:** Crossing, Finishing, Heading, Accuracy, ShortPassing, Volleys, Dribbling, Curve, FKAccuracy, LongPassing, BallControl, Acceleration, SprintSpeed, Agility, Reactions, Balance, ShotPower, Jumping, Stamina, Strength, LongShots, Aggression, Interceptions, Positioning, Vision, Penalties, Composure, Marking, StandingTackle, SlidingTackle, GKDiving, GKHandling, GKKicking, GKPositioning, GKReflexes, and Release Clause.

**Source:** https://www.kaggle.com/karangadiya/fifa19

Use the .toPandas() method to view the first few lines of the dataset so we know what we are working with. 

In [ ]:
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_colwidth',None)
pd.set_option('display.max_rows',None)
df.toPandas().head()

_c0      ID               Name  Age  \
0    0  158023           L. Messi   31   
1    1   20801  Cristiano Ronaldo   33   
2    2  190871          Neymar Jr   26   
3    3  193080             De Gea   27   
4    4  192985       K. De Bruyne   27   

                                            Photo Nationality  \
0  https://cdn.sofifa.org/players/4/19/158023.png   Argentina   
1   https://cdn.sofifa.org/players/4/19/20801.png    Portugal   
2  https://cdn.sofifa.org/players/4/19/190871.png      Brazil   
3  https://cdn.sofifa.org/players/4/19/193080.png       Spain   
4  https://cdn.sofifa.org/players/4/19/192985.png     Belgium   

                                  Flag  Overall  Potential  \
0  https://cdn.sofifa.org/flags/52.png       94         94   
1  https://cdn.sofifa.org/flags/38.png       94         94   
2  https://cdn.sofifa.org/flags/54.png       92         93   
3  https://cdn.sofifa.org/flags/45.png       91         93   
4   https://cdn.sofifa.org/flags/7.png       91         92   

                  Club                                     Club Logo    Value  \
0         FC Barcelona  https://cdn.sofifa.org/teams/2/light/241.png  €110.5M   
1             Juventus   https://cdn.sofifa.org/teams/2/light/45.png     €77M   
2  Paris Saint-Germain   https://cdn.sofifa.org/teams/2/light/73.png  €118.5M   
3    Manchester United   https://cdn.sofifa.org/teams/2/light/11.png     €72M   
4      Manchester City   https://cdn.sofifa.org/teams/2/light/10.png    €102M   

    Wage  Special Preferred Foot  International Reputation  Weak Foot  \
0  €565K     2202           Left                       5.0        4.0   
1  €405K     2228          Right                       5.0        4.0   
2  €290K     2143          Right                       5.0        5.0   
3  €260K     1471          Right                       4.0        3.0   
4  €355K     2281          Right                       4.0        5.0   

   Skill Moves       Work Rate   Body Type Real Face Position  Jersey Number  \
0          4.0  Medium/ Medium       Messi       Yes       RF           10.0   
1          5.0       High/ Low  C. Ronaldo       Yes       ST            7.0   
2          5.0    High/ Medium      Neymar       Yes       LW           10.0   
3          1.0  Medium/ Medium        Lean       Yes       GK            1.0   
4          4.0      High/ High      Normal       Yes      RCM            7.0   

         Joined Loaned From Contract Valid Until Height  Weight    LS    ST  \
0   Jul 1, 2004        None                 2021    5'7  159lbs  88+2  88+2   
1  Jul 10, 2018        None                 2022    6'2  183lbs  91+3  91+3   
2   Aug 3, 2017        None                 2022    5'9  150lbs  84+3  84+3   
3   Jul 1, 2011        None                 2020    6'4  168lbs  None  None   
4  Aug 30, 2015        None                 2023   5'11  154lbs  82+3  82+3   

     RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM    CM  \
0  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2  84+2   
1  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3  81+3  81+3   
2  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3  81+3  81+3   
3  None  None  None  None  None  None  None  None  None  None  None  None   
4  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3  88+3  87+3  87+3   

    RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB    RB  \
0  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2  47+2  59+2   
1  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3  53+3  53+3  61+3   
2  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3  47+3  47+3  60+3   
3  None  None  None  None  None  None  None  None  None  None  None  None   
4  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3  66+3  66+3  73+3   

   Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  Dribbling  \
0      84.0       95.0             70.0          90.0     86.0       97.0   
1      84.0       94.0  

Now print the schema of the dataset so we can see the data types of all the varaibles. 

In [ ]:
df.printSchema()

root
 |-- _c0: integer (nullable = true)
 |-- ID: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Age: integer (nullable = true)
 |-- Photo: string (nullable = true)
 |-- Nationality: string (nullable = true)
 |-- Flag: string (nullable = true)
 |-- Overall: integer (nullable = true)
 |-- Potential: integer (nullable = true)
 |-- Club: string (nullable = true)
 |-- Club Logo: string (nullable = true)
 |-- Value: string (nullable = true)
 |-- Wage: string (nullable = true)
 |-- Special: integer (nullable = true)
 |-- Preferred Foot: string (nullable = true)
 |-- International Reputation: integer (nullable = true)
 |-- Weak Foot: integer (nullable = true)
 |-- Skill Moves: integer (nullable = true)
 |-- Work Rate: string (nullable = true)
 |-- Body Type: string (nullable = true)
 |-- Real Face: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- Jersey Number: integer (nullable = true)
 |-- Joined: string (nullable = true)
 |-- Loaned From: string (nu

## Now let's get started!

### First things first..... import the pyspark sql functions library

Since we know we will be using it a lot.

In [ ]:
from pyspark.sql import functions

### 1. Select the Name and Position of each player in the dataframe

In [ ]:
df.select('Name','Position').toPandas()

Name Position
0                    L. Messi       RF
1           Cristiano Ronaldo       ST
2                   Neymar Jr       LW
3                      De Gea       GK
4                K. De Bruyne      RCM
5                   E. Hazard       LF
6                   L. Modrić      RCM
7                   L. Suárez       RS
8                Sergio Ramos      RCB
9                    J. Oblak       GK
10             R. Lewandowski       ST
11                   T. Kroos      LCM
12                   D. Godín       CB
13                David Silva      LCM
14                   N. Kanté      LDM
15                  P. Dybala       LF
16                    H. Kane       ST
17               A. Griezmann      CAM
18              M. ter Stegen       GK
19                T. Courtois       GK
20            Sergio Busquets      CDM
21                  E. Cavani       LS
22                   M. Neuer       GK
23                  S. Agüero       ST
24               G. Chiellini      LCB
25                  K. Mbappé       RM
26                   M. Salah       RM
27                   Casemiro      CDM
28               J. Rodríguez      LAM
29                 L. Insigne       LW
30                       Isco       LW
31                 C. Eriksen      CAM
32                   Coutinho       LW
33              P. Aubameyang       LM
34                 M. Hummels      LCB
35                    Marcelo       LB
36                    G. Bale       ST
37                  H. Lloris       GK
38                 G. Higuaín       LS
39               Thiago Silva      RCB
40              S. Handanovič       GK
41                  G. Buffon       GK
42                  S. Umtiti       CB
43                  M. Icardi       ST
44               K. Koulibaly      LCB
45                   P. Pogba      RDM
46                   K. Navas       GK
47                  R. Lukaku       ST
48                C. Immobile       ST
49                 Jordi Alba       LB
50                 D. Mertens       RF
51              J. Vertonghen      LCB
52                  M. Hamšík      LCM
53                 I. Rakitić      RCM
54                      Piqué      RCB
55                    L. Sané       LW
56             Bernardo Silva       RW
57                    Ederson       GK
58                    S. Mané       LM
59                V. van Dijk      LCB
60                R. Sterling       RW
61            Roberto Firmino      CAM
62                  R. Varane      RCB
63                M. Verratti      LCM
64                Alex Sandro       LB
65              Douglas Costa       LM
66                  T. Müller      CAM
67                     Thiago       CM
68                    M. Reus       LM
69                Azpilicueta       RB
70                 L. Bonucci      RCB
71            T. Alderweireld      RCB
72                  M. Pjanić      CDM
73                 M. Benatia       CB
74                    M. Özil      CAM
75                Fernandinho      CDM
76                    Iniesta       LF
77                M. Škriniar      LCB
78        S. Milinković-Savić       CM
79              Marco Asensio       RW
80                   N. Fekir      CAM
81                    Alisson       GK
82                 J. Kimmich      RCM
83                       Saúl      RCM
84                  R. Mahrez       RW
85                   D. Alaba       LB
86                       Koke       LM
87               A. Lacazette       ST
88                 K. Manolas      LCB
89                N. Otamendi       CB
90                     Parejo      RCM
91                   Paulinho      LDM
92                W. Szczęsny       GK
93                 A. Sánchez       RW
94                 Y. Brahimi       LM
95                 J. Boateng      RCB
96                   A. Vidal      CAM
97                 I. Perišić       LM
98                   E. Džeko       ST
99                 S. Khedira      RCM
100               Diego Costa       LS
101             R. Nainggolan      CAM
102     

### 1.1 Display the same results from above sorted by the players names

In [ ]:
df.select('Name',"Position").orderBy('Name').toPandas().head(10)

Name Position
0        A. Abang       ST
1   A. Abdellaoui       LB
2    A. Abdennour       CB
3         A. Abdi       CM
4   A. Abdu Jaber       ST
5  A. Abdulhameed       GK
6    A. Abedzadeh       GK
7        A. Abeid       LB
8        A. Ablet      LWB
9      A. Abrashi      CDM

### 2. Select only the players who belong to a club begining with FC

In [ ]:
df.where(df.Club.startswith('FC')).limit(5).toPandas()

_c0      ID             Name  Age  \
0    0  158023         L. Messi   31   
1    7  176580        L. Suárez   31   
2   10  188545   R. Lewandowski   29   
3   18  192448    M. ter Stegen   26   
4   20  189511  Sergio Busquets   29   

                                            Photo Nationality  \
0  https://cdn.sofifa.org/players/4/19/158023.png   Argentina   
1  https://cdn.sofifa.org/players/4/19/176580.png     Uruguay   
2  https://cdn.sofifa.org/players/4/19/188545.png      Poland   
3  https://cdn.sofifa.org/players/4/19/192448.png     Germany   
4  https://cdn.sofifa.org/players/4/19/189511.png       Spain   

                                  Flag  Overall  Potential               Club  \
0  https://cdn.sofifa.org/flags/52.png       94         94       FC Barcelona   
1  https://cdn.sofifa.org/flags/60.png       91         91       FC Barcelona   
2  https://cdn.sofifa.org/flags/37.png       90         90  FC Bayern München   
3  https://cdn.sofifa.org/flags/21.png       89         92       FC Barcelona   
4  https://cdn.sofifa.org/flags/45.png       89         89       FC Barcelona   

                                      Club Logo    Value   Wage  Special  \
0  https://cdn.sofifa.org/teams/2/light/241.png  €110.5M  €565K     2202   
1  https://cdn.sofifa.org/teams/2/light/241.png     €80M  €455K     2346   
2   https://cdn.sofifa.org/teams/2/light/21.png     €77M  €205K     2152   
3  https://cdn.sofifa.org/teams/2/light/241.png     €58M  €240K     1328   
4  https://cdn.sofifa.org/teams/2/light/241.png   €51.5M  €315K     2065   

  Preferred Foot  International Reputation  Weak Foot  Skill Moves  \
0           Left                         5          4            4   
1          Right                         5          4            3   
2          Right                         4          4            4   
3          Right                         3          4            1   
4          Right                         4          3            3   

        Work Rate Body Type Real Face Position  Jersey Number        Joined  \
0  Medium/ Medium     Messi       Yes       RF             10   Jul 1, 2004   
1    High/ Medium    Normal       Yes       RS              9  Jul 11, 2014   
2    High/ Medium    Normal       Yes       ST              9   Jul 1, 2014   
3  Medium/ Medium    Normal       Yes       GK             22   Jul 1, 2014   
4  Medium/ Medium      Lean       Yes      CDM              5   Sep 1, 2008   

  Loaned From Contract Valid Until Height  Weight    LS    ST    RS    LW  \
0        None                 2021    5'7  159lbs  88+2  88+2  88+2  92+2   
1        None                 2021    6'0  190lbs  87+5  87+5  87+5  86+5   
2        None                 2021    6'0  176lbs  87+3  87+3  87+3  83+3   
3        None                 2022    6'2  187lbs  None  None  None  None   
4        None                 2023    6'2  168lbs  71+3  71+3  71+3  74+3   

     LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM    CM   RCM    RM  \
0  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2  84+2  84+2  91+2   
1  87+5  87+5  87+5  86+5  85+5  85+5  85+5  84+5  79+5  79+5  79+5  84+5   
2  86+3  86+3  86+3  83+3  83+3  83+3  83+3  81+3  77+3  77+3  77+3  81+3   
3  None  None  None  None  None  None  None  None  None  None  None  None   
4  76+3  76+3  76+3  74+3  79+3  79+3  79+3  76+3  83+3  83+3  83+3  76+3   

    LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB    RB  Crossing  \
0  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2  47+2  59+2        84   
1  69+5  68+5  68+5  68+5  69+5  66+5  63+5  63+5  63+5  66+5        77   
2  61+3  62+3  62+3  62+3  61+3  58+3  57+3  57+3  57+3  58+3        62   
3  None  None  None  None  None  None  None  None  None  None        15   
4  79+3  86+3  86+3  86+3  79+3  78+3  82+3  82+3  82+3  78+3        62   

   Finishing  HeadingAccuracy  ShortPassing  Volleys  Dribbling  Curve  \
0         95               70            90       86         97     93   
1     

### 3. Who is the oldest player in the dataset and how old are they?

Display only the name and age of the oldest player.

In [ ]:
df.select('Name','Age').orderBy(df.Age.desc()).limit(1).show()

+--------+---+
|    Name|Age|
+--------+---+
|O. Pérez| 45|
+--------+---+



### 4. Select only the following players from the dataframe:

 - L. Messi
 - Cristiano Ronaldo

In [ ]:
df.where("Name == 'L. Messi'  or Name == 'Cristiano Ronaldo'").show()

+---+------+-----------------+---+--------------------+-----------+--------------------+-------+---------+------------+--------------------+-------+-----+-------+--------------+------------------------+---------+-----------+--------------+----------+---------+--------+-------------+------------+-----------+--------------------+------+------+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+--------+---------+---------------+------------+-------+---------+-----+----------+-----------+-----------+------------+-----------+-------+---------+-------+---------+-------+-------+--------+---------+----------+-------------+-----------+------+---------+---------+-------+--------------+-------------+--------+----------+---------+-------------+----------+--------------+
|_c0|    ID|             Name|Age|               Photo|Nationality|                Flag|Overall|Potential|        Club|           Club Logo|  Value| Wag

### 5. Can you select the first character from the Release Clause variable which indicates the currency used?

In [ ]:
df.select('Name', df["Release Clause"].substr(1,1)).show(5)

+-----------------+-------------------------------+
|             Name|substring(Release Clause, 1, 1)|
+-----------------+-------------------------------+
|         L. Messi|                              €|
|Cristiano Ronaldo|                              €|
|        Neymar Jr|                              €|
|           De Gea|                              €|
|     K. De Bruyne|                              €|
+-----------------+-------------------------------+
only showing top 5 rows



### 6. Can you select only the players who are over the age of 40?

In [ ]:
df.filter('Age>40').toPandas()

_c0      ID           Name  Age  \
0   1120  156092      J. Villar   41   
1   4228    3665       B. Nivet   41   
2   4741  140029       O. Pérez   45   
3   7225  142998       C. Muñoz   41   
4  10545  140183    S. Narazaki   42   
5  12192  208927   H. Sulaimani   41   
6  15426   18745       M. Tyler   41   
7  17726   51963      T. Warner   44   
8  18183   53748  K. Pilkington   44   

                                            Photo        Nationality  \
0  https://cdn.sofifa.org/players/4/19/156092.png           Paraguay   
1    https://cdn.sofifa.org/players/4/19/3665.png             France   
2  https://cdn.sofifa.org/players/4/19/140029.png             Mexico   
3  https://cdn.sofifa.org/players/4/19/142998.png          Argentina   
4  https://cdn.sofifa.org/players/4/19/140183.png              Japan   
5  https://cdn.sofifa.org/players/4/19/208927.png       Saudi Arabia   
6   https://cdn.sofifa.org/players/4/19/18745.png            England   
7   https://cdn.sofifa.org/players/4/19/51963.png  Trinidad & Tobago   
8   https://cdn.sofifa.org/players/4/19/53748.png            England   

                                   Flag  Overall  Potential  \
0   https://cdn.sofifa.org/flags/58.png       77         77   
1   https://cdn.sofifa.org/flags/18.png       71         71   
2   https://cdn.sofifa.org/flags/83.png       71         71   
3   https://cdn.sofifa.org/flags/52.png       68         68   
4  https://cdn.sofifa.org/flags/163.png       65         65   
5  https://cdn.sofifa.org/flags/183.png       63         63   
6   https://cdn.sofifa.org/flags/14.png       59         59   
7   https://cdn.sofifa.org/flags/93.png       53         53   
8   https://cdn.sofifa.org/flags/14.png       48         48   

                           Club  \
0                          None   
1                  ESTAC Troyes   
2                       Pachuca   
3  CD Universidad de Concepción   
4                Nagoya Grampus   
5                     Ohod Club   
6           Peterborough United   
7            Accrington Stanley   
8              Cambridge United   

                                         Club Logo  Value Wage  Special  \
0              https://cdn.sofifa.org/flags/58.png     €0   €0     1168   
1     https://cdn.sofifa.org/teams/2/light/294.png     €0  €5K     1785   
2  https://cdn.sofifa.org/teams/2/light/110147.png  €160K  €8K     1256   
3  https://cdn.sofifa.org/teams/2/light/112534.png   €60K  €1K     1234   
4  https://cdn.sofifa.org/teams/2/light/112092.png   €40K  €1K     1296   
5  https://cdn.sofifa.org/teams/2/light/113219.png     €0  €3K     1842   
6    https://cdn.sofifa.org/teams/2/light/1938.png   €10K  €1K     1031   
7  https://cdn.sofifa.org/teams/2/light/110313.png     €0  €1K      926   
8    https://cdn.sofifa.org/teams/2/light/1944.png     €0  €1K      774   

  Preferred Foot  International Reputation  Weak Foot  Skill Moves  \
0          Right                         2          3            1   
1          Right                         2          3            3   
2          Right                         2          3            1   
3          Right                         1          3            1   
4          Right                         2          3            1   
5           Left                         1          3            3   
6          Right                         1          3            1   
7          Right                         1          2            1   
8          Right                         1          2            1   

        Work Rate Body Type Real Face Position  Jersey Number        Joined  \
0  Medium/ Medium    Normal        No       GK              1          None   
1  Medium/ Medium    Normal        No      CAM             10   Jul 1, 2012   
2  Medium/ Medium    Stocky        No       GK             21   Jun 1, 1991   
3  Medium/ Medium    Normal        No       GK              1   Jan 1, 2013   
4  Medium/ Medium    Normal        No       GK        

### That's is for now... Great Job!